#EDA

In [ ]:
!pip install osmnx folium geopandas --quiet

In [ ]:
import osmnx as ox
import folium
import ast
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point

Для начала посмотрим границы, в которых проводим анализ - Басманный район Москвы. В дальнейшем будем наносить точки заведений именно в этих границах:

In [ ]:
gdf = ox.geocode_to_gdf("Басманный район, Москва, Россия")


center = gdf.geometry.centroid.iloc[0]
m = folium.Map(location=[center.y, center.x], zoom_start=13)


folium.GeoJson(
    gdf,
    name="Басманный район",
    style_function=lambda x: {"fillColor": "lightblue", "color": "blue", "weight": 2, "fillOpacity": 0.3}
).add_to(m)

m

/tmp/ipython-input-3591665992.py:4: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  center = gdf.geometry.centroid.iloc[0]


Небольшая предобрабокта координат:

In [ ]:
cafes = pd.read_json('/content/basman_cafes.json')
cafes.head(10)

name  type osm_type                      address      cuisine  \
0                Com  cafe     node                                vietnamese   
1        Шоколадница  cafe     node                               coffee_shop   
2          Кофе Хауз  cafe     node                               coffee_shop   
3          Алтаргана  cafe     node                                    buryat   
4             Буржуй  cafe     node  Нижняя Красносельская улица      russian   
5           Kalabasa  cafe     node                                      cake   
6           Погребок  cafe     node                                             
7  Кафе на Басманной  cafe     node                                             
8           БлинБери  cafe     node                                     crepe   
9            Тбилисо  cafe     node                                  georgian   

  rating             website                                      coordinates  
0                              {'longitude': 37.644618, 'latitude': 55.76828}  
1                             {'longitude': 37.631644, 'latitude': 55.757364}  
2                             {'longitude': 37.658665, 'latitude': 55.757643}  
3                             {'longitude': 37.652294, 'latitude': 55.767346}  
4         www.burjui-club.ru   {'longitude': 37.67189, 'latitude': 55.774863}  
5                             {'longitude': 37.679773, 'latitude': 55.762531}  
6                             {'longitude': 37.634187, 'latitude': 55.761781}  
7                             {'longitude': 37.668711, 'latitude': 55.768943}  
8                             {'longitude': 37.639685, 'latitude': 55.764734}  
9                             {'longitude': 37.679352, 'latitude': 55.768274}

In [ ]:
# извлечем координаты из колонки coordinates
def to_lat_lon(x):
    if pd.isna(x):
        return None, None
    if isinstance(x, str):
        try:
            x = ast.literal_eval(x)  # парсим строку в dict
        except Exception:
            return None, None
    try:
        return x.get('latitude'), x.get('longitude')
    except Exception:
        return None, None

cafes[['lat', 'lon']] = cafes['coordinates'].apply(lambda v: pd.Series(to_lat_lon(v)))
cafes.drop(columns = ['coordinates'], inplace = True)
cafes.head(10)

name  type osm_type                      address      cuisine  \
0                Com  cafe     node                                vietnamese   
1        Шоколадница  cafe     node                               coffee_shop   
2          Кофе Хауз  cafe     node                               coffee_shop   
3          Алтаргана  cafe     node                                    buryat   
4             Буржуй  cafe     node  Нижняя Красносельская улица      russian   
5           Kalabasa  cafe     node                                      cake   
6           Погребок  cafe     node                                             
7  Кафе на Басманной  cafe     node                                             
8           БлинБери  cafe     node                                     crepe   
9            Тбилисо  cafe     node                                  georgian   

  rating             website        lat        lon  
0                             55.768280  37.644618  
1                             55.757364  37.631644  
2                             55.757643  37.658665  
3                             55.767346  37.652294  
4         www.burjui-club.ru  55.774863  37.671890  
5                             55.762531  37.679773  
6                             55.761781  37.634187  
7                             55.768943  37.668711  
8                             55.764734  37.639685  
9                             55.768274  37.679352

Нанесем расположения кафешек синими точками на карту:

In [ ]:
for name, cuisine, lat, lon in zip(cafes['name'], cafes['cuisine'], cafes['lat'], cafes['lon']):
    popup_html = f"""
    <b>{name}</b><br>
    cuisine: {cuisine or '—'}<br>
    {lat:.6f}; {lon:.6f}
    """

    folium.CircleMarker(
        location=[lat, lon],
        radius=5,
        color="blue",
        fill=True,
        fill_opacity=0.8,
        tooltip=name
    ).add_to(m).add_child(
        folium.Popup(popup_html, max_width=250)
    )

m

Теперь прицельно посмотрим на расположение кафешек с типом "кофешоп" ('cuisine' == 'coffee_shop') и выделим области красным, в которых в радиусе 200м попадает 3 таких кафешки или больше

In [ ]:
# точки с типом кухни = кофешоп
coffee = cafes.loc[cafes['cuisine'] == 'coffee_shop', ['name', 'cuisine', 'lat', 'lon']].dropna()

# геометрия и буферы
gdf = gpd.GeoDataFrame(
    coffee,
    geometry=gpd.points_from_xy(coffee['lon'], coffee['lat']),
    crs="EPSG:4326"
).to_crs(3857)

buf = gdf.copy()
buf['geometry'] = gdf.geometry.buffer(200)  # радиус 200 м

# считаем количество соседей
j = gpd.sjoin(buf[['geometry']], gdf[['geometry']], predicate='contains', how='left')
counts = j.groupby(j.index).size()
dense_buf = buf.loc[counts[counts >= 3].index]

# слияние пересекающихся областей
if not dense_buf.empty:
    merged = dense_buf.unary_union
    regions = (
        gpd.GeoDataFrame(
            geometry=[merged] if merged.geom_type != 'MultiPolygon' else list(merged.geoms),
            crs="EPSG:3857"
        ).to_crs(4326)
    )

    folium.GeoJson(
        data=regions.__geo_interface__,
        name="Зоны с ≥3 кофейнями в 200 м",
        style_function=lambda _: {
            "fillColor": "red",
            "color": "darkred",
            "weight": 2,
            "fillOpacity": 0.3,
        },
    ).add_to(m)

# добавляем точки с popup и tooltip
for name, cuisine, lat, lon in zip(cafes['name'], cafes['cuisine'], cafes['lat'], cafes['lon']):
    popup_html = f"""
    <b>{name}</b><br>
    cuisine: {cuisine or '—'}<br>
    {lat:.6f}; {lon:.6f}
    """
    folium.CircleMarker(
        location=[lat, lon],
        radius=5,
        color="blue",
        fill=True,
        fill_opacity=0.8,
        tooltip=name,  #подсказка при наведении
    ).add_to(m).add_child(
        folium.Popup(popup_html, max_width=250)
    )


m

/tmp/ipython-input-2365702299.py:21: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  merged = dense_buf.unary_union


Нанесем на карту ж\д станции и станции метро зелёными точками

In [ ]:
transport = pd.read_json('/content/basman_transport_data.json')
transport[['lat', 'lon']] = transport['coordinates'].apply(lambda v: pd.Series(to_lat_lon(v)))
transport.drop(columns = ['coordinates'], inplace = True)
transport.head(10)

name osm_type  \
0                 Москва-Пассажирская-Курская     node   
1                                  Бауманская     node   
2  Малый Демидовский переулок, школа акварели     node   
3                           Токмаков переулок     node   
4                         Спартаковская улица     node   
5                        Технический переулок     node   
6                          Метро «Бауманская»     node   
7                      Балакиревский переулок     node   
8                      Спартаковский переулок     node   
9               Доброслободская улица — Театр     node   

                                                tags address        lat  \
0  {'public_transport': 'station', 'railway': 'st...          55.757678   
1  {'public_transport': 'station', 'railway': 'st...          55.773039   
2  {'public_transport': 'platform', 'railway': ''...          55.765005   
3  {'public_transport': 'platform', 'railway': ''...          55.765234   
4  {'public_transport': 'platform', 'railway': ''...          55.771744   
5  {'public_transport': 'platform', 'railway': ''...          55.763481   
6  {'public_transport': 'platform', 'railway': ''...          55.773276   
7  {'public_transport': 'platform', 'railway': ''...          55.777846   
8  {'public_transport': 'platform', 'railway': ''...          55.775918   
9  {'public_transport': 'platform', 'railway': ''...          55.764327   

         lon  
0  37.662788  
1  37.680549  
2  37.664926  
3  37.670462  
4  37.668386  
5  37.682138  
6  37.679268  
7  37.690096  
8  37.686428  
9  37.673962

In [ ]:
# станции ж\д и метро
stations = transport[
    transport['tags'].apply(
        lambda x: isinstance(x, dict) and x.get('railway') == 'station'
    )
]
stations


name osm_type  \
0   Москва-Пассажирская-Курская     node   
1                    Бауманская     node   
11                      Курская     node   
45                  Китай-город     node   
46                   Чкаловская     node   
50             Электрозаводская     node   

                                                 tags address        lat  \
0   {'public_transport': 'station', 'railway': 'st...          55.757678   
1   {'public_transport': 'station', 'railway': 'st...          55.773039   
11  {'public_transport': 'station', 'railway': 'st...          55.757198   
45  {'public_transport': 'station', 'railway': 'st...          55.755652   
46  {'public_transport': 'station', 'railway': 'st...          55.756702   
50  {'public_transport': 'station', 'railway': 'st...          55.780285   

          lon  
0   37.662788  
1   37.680549  
11  37.659332  
45  37.633565  
46  37.656998  
50  37.702993

In [ ]:
for name, lat, lon in zip(stations['name'], stations['lat'], stations['lon']):
    popup_html = f"""
    <b>{name}</b><br>
    {lat:.6f}; {lon:.6f}
    """
    folium.CircleMarker(
        location=[lat, lon],
        radius=6,
        color="#39FF14",
        fill=True,
        fill_color="#39FF14",
        fill_opacity=0.9,
        tooltip=name  # показываем название при наведении
    ).add_to(m).add_child(
        folium.Popup(popup_html, max_width=250)
    )

m

На карте видно, что наибольшее скопление красных областей приходится на территории вдоль железнодорожного узла "Москва Пассажирская-Курская". Вторым местом большого скопления кафе является область вокруг станции метро "Бауманская". Можно выдвинуть гипотезу о том, что популярным месторасположением для открытия кафе является зона вблизи транспортных узлов

Теперь добавим университеты, колледжи и школы розовым цветом на карту:

In [ ]:
edu = pd.read_json('/content/basman_complete_education.json')
edu[['lat', 'lon']] = edu['coordinates'].apply(lambda v: pd.Series(to_lat_lon(v)))
edu.drop(columns = ['coordinates'], inplace = True)
uni = edu[(edu['type'] == 'university') | (edu['type'] == 'college') | (edu['type'] == 'school') ]
uni.head(10)


name        type osm_type  \
0                                          Школа №435      school     node   
3   Свято-Филаретовский православно-христианский и...  university     node   
4   Институт Психологии и Психоанализа на Чистых п...  university     node   
5         Московская театральная школа Олега Табакова     college     node   
8                        Российский новый университет  university     node   
11           Международный институт экономики и права  university     node   
14                    Британская высшая школа дизайна  university     node   
24     Московский художественно-промышленный институт  university     node   
25  Институт лингвистики и межкультурной коммуникации  university     node   
31                  МГТУ им. Н. Э. Баумана (Корпус Э)  university      way   

                    address        lat        lon  
0                            55.774614  37.704853  
3            улица Покровка  55.760716  37.648185  
4                            55.760766  37.646290  
5                            55.761804  37.649313  
8               улица Радио  55.762665  37.682171  
11    Рубцовская набережная  55.776605  37.699817  
14                           55.751664  37.669866  
24                           55.763634  37.682392  
25                           55.777762  37.684180  
31  Лефортовская набережная  55.768852  37.689622

In [ ]:
for name, lat, lon in zip(uni['name'], uni['lat'], uni['lon']):
    popup_html = f"""
    <b>{name}</b><br>
    {lat:.6f}; {lon:.6f}
    """
    folium.CircleMarker(
        location=[lat, lon],
        radius=6,
        color="#BF00FF",
        fill=True,
        fill_color="#BF00FF",
        fill_opacity=0.9,
        tooltip=name  # показываем название при наведении
    ).add_to(m).add_child(
        folium.Popup(popup_html, max_width=250)
    )

m

Как видно на карте, каких-то отчётливых зависимостей месторасположения кафе от расположения образовательных заведений не прослеживается. К примеру, вокруг МГТУ им. Баумана нет скоплений кафе.
Близость школ также предположительно не влияет на выбор локации для кафе: четыре школы на стороне Семёновской набережной вообще не имеют ни одного кафе поблизости

### Вывод:
Основная гипотеза - наибольшую привлекательность для откытия кафе типа "coffee shop" имеют локации вблизи транспотных узлов, таких как станции метро и вокзалы
Близость же образовательных учреждений предположительно не несет какой-то особой значимости при выборе локации для открытия кафе, т.к. скоплений кофешопов вблизи школ, университетов или колледжей нет